In [63]:
import torch
from torch_geometric.data import Data
from torch_geometric.loader import DataLoader
import torch.nn as nn
from torch.optim import Adam
import torch_geometric.nn as pyg_nn
from sklearn.preprocessing import LabelEncoder
import pandas as pd

edge_list_df = pd.read_csv("EdgeList.csv", sep=";")
diatom_inventory_df = pd.read_csv("DiatomInventories_GTstudentproject.csv", sep=";")
pressure_status_df = pd.read_csv("PressureStatus_GTstudentproject.csv", sep=";")

In [64]:
pressure_status_df['Nitrogencompounds_Status1Y'].unique()

array(['Good', 'Bad', 'Moderate', 'High', 'Poor', 'Unassessed'],
      dtype=object)

In [65]:
edge_list_df['Cooc'] = edge_list_df['Cooc'].str.replace(',', '.').astype(float)
diatom_inventory_df['Abundance_pm'] = diatom_inventory_df['Abundance_pm'].str.replace(',', '.').astype(float)

# trying a binary mapping after trying 5 classes 
status_mapping = {'High': 1, 'Good': 1, 'Moderate': 0, 'Poor': 0, 'Bad': 0}
pressure_status_df = pressure_status_df[pressure_status_df['Nitrogencompounds_Status1Y'] != 'Unassessed']
pressure_status_df['Nitrogencompounds_Status1Y'] = pressure_status_df['Nitrogencompounds_Status1Y'].map(status_mapping)

diatom_inventory_df = diatom_inventory_df.merge(pressure_status_df[['SamplingOperations_code', 'Nitrogencompounds_Status1Y']], on='SamplingOperations_code', how='left')

In [66]:
diatom_inventory_df.head()

TaxonName TaxonCode SamplingOperations_code  \
0  Achnanthes aapajaervensis   Achaa01      S04094200_20120910   
1  Achnanthes aapajaervensis   Achaa01      S05155300_20100728   
2         Achnanthes affinis   Achaf01      S02018780_20070808   
3         Achnanthes affinis   Achaf01      S02022675_20090803   
4         Achnanthes affinis   Achaf01      S02094920_20120726   

  CodeSite_SamplingOperations Date_SamplingOperation  Abundance_nbcell  \
0                   S04094200             2012-09-10                 8   
1                   S05155300             2010-07-28                 1   
2                   S02018780             2007-08-08                 1   
3                   S02022675             2009-08-03                 2   
4                   S02094920             2012-07-26                 1   

   TotalAbundance_SamplingOperation  Abundance_pm  Nitrogencompounds_Status1Y  
0                               420     19.047619                         1.0  
1                               404      2.475248                         1.0  
2                               400      2.500000                         1.0  
3                               400      5.000000                         1.0  
4                               400      2.500000                         1.0

In [67]:

diatom_inventory_df = diatom_inventory_df.dropna(subset=['Nitrogencompounds_Status1Y']) # drop any rows that nitrogen compounds not assessed for

In [68]:
diatom_inventory_df.head()

TaxonName TaxonCode SamplingOperations_code  \
0  Achnanthes aapajaervensis   Achaa01      S04094200_20120910   
1  Achnanthes aapajaervensis   Achaa01      S05155300_20100728   
2         Achnanthes affinis   Achaf01      S02018780_20070808   
3         Achnanthes affinis   Achaf01      S02022675_20090803   
4         Achnanthes affinis   Achaf01      S02094920_20120726   

  CodeSite_SamplingOperations Date_SamplingOperation  Abundance_nbcell  \
0                   S04094200             2012-09-10                 8   
1                   S05155300             2010-07-28                 1   
2                   S02018780             2007-08-08                 1   
3                   S02022675             2009-08-03                 2   
4                   S02094920             2012-07-26                 1   

   TotalAbundance_SamplingOperation  Abundance_pm  Nitrogencompounds_Status1Y  
0                               420     19.047619                         1.0  
1                               404      2.475248                         1.0  
2                               400      2.500000                         1.0  
3                               400      5.000000                         1.0  
4                               400      2.500000                         1.0

In [69]:
diatom_inventory_df['Nitrogencompounds_Status1Y'].unique()

array([1., 0.])

In [70]:
sampled_samplings = diatom_inventory_df['SamplingOperations_code'].dropna().sample(n=10000, random_state=42).unique() # since code takes a bit, testing smaller sections
diatom_inventory_subset = diatom_inventory_df[diatom_inventory_df['SamplingOperations_code'].isin(sampled_samplings)]

In [71]:
diatom_inventory_subset.head()

TaxonName TaxonCode SamplingOperations_code  \
3   Achnanthes affinis   Achaf01      S02022675_20090803   
6   Achnanthes affinis   Achaf01      S02096950_20070911   
8   Achnanthes affinis   Achaf01      S02110650_20080730   
10  Achnanthes affinis   Achaf01      S02117585_20080731   
11  Achnanthes affinis   Achaf01      S02122200_20070731   

   CodeSite_SamplingOperations Date_SamplingOperation  Abundance_nbcell  \
3                    S02022675             2009-08-03                 2   
6                    S02096950             2007-09-11                 1   
8                    S02110650             2008-07-30                 1   
10                   S02117585             2008-07-31                 6   
11                   S02122200             2007-07-31                 2   

    TotalAbundance_SamplingOperation  Abundance_pm  Nitrogencompounds_Status1Y  
3                                400           5.0                         1.0  
6                                400           2.5                         1.0  
8                                400           2.5                         1.0  
10                               400          15.0                         1.0  
11                               400           5.0                         1.0

In [72]:
# create a subgraph of taxa for each sampling operation
subgraphs = []

for sampling_code, group in diatom_inventory_subset.groupby('SamplingOperations_code'):
    relevant_taxa = group['TaxonCode'].unique()
    taxon_to_index = {taxon: idx for idx, taxon in enumerate(relevant_taxa)}
    subgraph_edges = edge_list_df[edge_list_df['TaxonCode_1'].isin(relevant_taxa) & edge_list_df['TaxonCode_2'].isin(relevant_taxa)]
    subgraph_edges['Source_idx'] = subgraph_edges['TaxonCode_1'].map(taxon_to_index)
    subgraph_edges['Target_idx'] = subgraph_edges['TaxonCode_2'].map(taxon_to_index)
    edge_index = torch.tensor(subgraph_edges[['Source_idx', 'Target_idx']].values.T, dtype=torch.long)
    node_features = group.groupby('TaxonCode')['Abundance_pm'].mean().reset_index()
    node_features = node_features.set_index('TaxonCode')['Abundance_pm'].to_dict()
    x = torch.tensor([node_features.get(taxon, 0) for taxon in relevant_taxa], dtype=torch.float).view(-1, 1)
    y = torch.tensor([int(group['Nitrogencompounds_Status1Y'].iloc[0])], dtype=torch.long) 
    
    subgraph = Data(x=x, edge_index=edge_index, y=y)
    subgraphs.append(subgraph)

num_subgraphs = len(subgraphs)
train_size = int(0.7 * num_subgraphs)
val_size = int(0.15 * num_subgraphs)
test_size = num_subgraphs - train_size - val_size

train_data = subgraphs[:train_size]
val_data = subgraphs[train_size:train_size + val_size]
test_data = subgraphs[train_size + val_size:]

train_loader = DataLoader(train_data, batch_size=32, shuffle=True)
val_loader = DataLoader(val_data, batch_size=32, shuffle=False)
test_loader = DataLoader(test_data, batch_size=32, shuffle=False)

class GNNModel(nn.Module):
    def __init__(self, num_node_features):
        super(GNNModel, self).__init__()
        self.conv1 = pyg_nn.GCNConv(num_node_features, 16)
        self.conv2 = pyg_nn.GCNConv(16, 32)
        self.fc = nn.Linear(32, 2) 

    def forward(self, data):
        x, edge_index = data.x, data.edge_index
        x = torch.relu(self.conv1(x, edge_index))
        x = torch.relu(self.conv2(x, edge_index))
        x = x.mean(dim=0)  
        x = self.fc(x)
        return x

model = GNNModel(num_node_features=1)
optimizer = Adam(model.parameters(), lr=0.001)
criterion = nn.CrossEntropyLoss()

num_epochs = 10
for epoch in range(num_epochs):
    model.train()
    for data in train_loader:
        optimizer.zero_grad()
        out = model(data)  
        # print(out)
        # print(data.y)
        loss = criterion(out.unsqueeze(0), y)  
        loss.backward()
        optimizer.step()

    model.eval()
    train_correct = 0
    val_correct = 0
    for data in train_loader:
        out = model(data)
        train_correct += (out.argmax() == data.y).sum().item() 
    for data in val_loader:
        out = model(data)
        val_correct += (out.argmax() == data.y).sum().item()  
    
    train_accuracy = train_correct / len(train_loader.dataset)
    val_accuracy = val_correct / len(val_loader.dataset)
    
    print(f'Epoch {epoch + 1}/{num_epochs}, Loss: {loss.item():.4f}, Train Accuracy: {train_accuracy:.4f}, Val Accuracy: {val_accuracy:.4f}')

model.eval()
test_correct = 0
for data in test_loader:
    out = model(data)
    test_correct += (out.argmax() == data.y).sum().item()

test_accuracy = test_correct / len(test_loader.dataset)
print(f'Test Accuracy: {test_accuracy:.4f}')


/var/folders/b1/w0t7phjx2_dfv3vn4w521y0r0000gn/T/ipykernel_71209/2845116094.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subgraph_edges['Source_idx'] = subgraph_edges['TaxonCode_1'].map(taxon_to_index)
/var/folders/b1/w0t7phjx2_dfv3vn4w521y0r0000gn/T/ipykernel_71209/2845116094.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  subgraph_edges['Target_idx'] = subgraph_edges['TaxonCode_2'].map(taxon_to_index)
/var/folders/b1/w0t7phjx2_dfv3vn4w521y0r0000gn/T/ipykernel_71209/2845116094.py:8: SettingWithC

Epoch 1/10, Loss: 0.0007, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 2/10, Loss: 0.0000, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 3/10, Loss: 0.0000, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 4/10, Loss: 0.0002, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 5/10, Loss: 0.0000, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 6/10, Loss: 0.0000, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 7/10, Loss: 0.0000, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 8/10, Loss: 0.0000, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 9/10, Loss: 0.0000, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Epoch 10/10, Loss: 0.0000, Train Accuracy: 0.9666, Val Accuracy: 0.9542
Test Accuracy: 0.9513
